# Université Paris-Saclay, Master 1 Mécanique des Fluides, Année 2022-2023

# _Méthodes Numériques pour la Mécanique des Fluides_

# Examen - 29 mars 2023 

Durée de l'épreuve : 3 heures

Documents de cours et de TP non autorisés

Les réponses seront données sur la **copie d'examen**, sauf pour les questions nécessitant de la programmation.

### Exercice : Résolution de l'équation de Burgers avec une méthode pseudo-spectrale

#### Approche fluide parfait

**4.** Dans le squelette de la fonction ```squelette_Burgers```, traduire l'équation du schéma discrétisé en instruction dans la boucle principale (ligne 32).

**5.** Compléter la définition de la fonction non-linéaire $\widehat{NL}_k$, à l'instant initial (ligne 23) et dans la boucle principale (ligne 45). On prendra soin d'utiliser le filtre défini à la ligne 12.


In [ ]:
import numpy as np

def squelette_burgers(Tf,dt,M):
    N=round(Tf/dt)

    x=np.arange(0,M)*2*np.pi/M
    t=np.arange(0,Tf,dt)

    k=np.concatenate([np.arange(0,M/2),np.arange(-M/2,0)])
    k2=k**2

    filt=np.abs(k)<(M/3)
    k=k*filt

    O1=1
    O2=1

    un=1+np.exp(-(x-np.pi)**2/.1)

    f_un=np.fft.fft(un)

    # instruction a completer question 5
    f_NLn= ...
    #
    f_NLnm1=np.copy(f_NLn)   

    Umat=np.zeros([M,N])   
    Umat[:,0]=np.real(np.fft.ifft(f_un*filt))

    for np1 in range(1,N):
        # instruction a completer question 4
        f_unp1= ...
        
        E=1/N*np.sum(np.sum(np.abs(f_unp1)**2))
        if E>1e+10:
            break        

        Umat[:,np1]=np.real(np.fft.ifft(f_unp1))
        
        f_un=np.copy(f_unp1)
        f_NLnm1=np.copy(f_NLn)

        # instruction a completer question 5
        f_NLn= ...
    return t, x, Umat

**6.** Appeler cette fonction avec les paramètres suivants : ```Tf=10```, ```dt=0.001```, ```M=1000```. 

In [ ]:
Tf=...
dt=...
M=...
t,x,Umat = squelette_burgers(Tf,dt,M)

Jouer ensuite l'animation du calcul avec le script suivant. Qu'observe-t-on? Quel est l'origine du problème?

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.animation
plt.rcParams["animation.html"] = "jshtml"
plt.ioff()

fig = plt.figure()
ax = fig.add_subplot(1, 1, 1)
time_template = 't = %.2fs'
time_text = ax.text(2,1.1,'') 
lin = ax.plot(x,Umat[:,0])
ax.set_xlabel('x')
ax.set_ylabel('y')

#sortie graphique
def update(n):
    ax.cla()
    lin = ax.plot(x,Umat[:,n])
    time_text.set_text(time_template%t[n])
    return lin, time_text

step=100
matplotlib.animation.FuncAnimation(fig, update, frames=range(0,round(round(Tf/dt)),step), repeat=False)    


#### Approche fluide visqueux

**8.** Implémenter ces modifications dans le code.

In [ ]:
import numpy as np

def squelette_burgers_dissipation(nu,Tf,dt,M):
    N=round(Tf/dt)

    x=np.arange(0,M)*2*np.pi/M
    t=np.arange(0,Tf,dt)

    k=np.concatenate([np.arange(0,M/2),np.arange(-M/2,0)])
    k2=k**2

    filt=np.abs(k)<(M/3)
    k=k*filt

    # instruction a completer question 7
    O1= ...
    O2= ... 

    un=1+np.exp(-(x-np.pi)**2/.1)

    f_un=np.fft.fft(un)

    # instruction a completer question 5
    f_NLn= ...
    #
    f_NLnm1=np.copy(f_NLn)   

    Umat=np.zeros([M,N])   
    Umat[:,0]=np.real(np.fft.ifft(f_un*filt))

    for np1 in range(1,N):
        # instruction a completer question 4
        f_unp1= ...
        
        E=1/N*np.sum(np.sum(np.abs(f_unp1)**2))
        if E>1e+10:
            break        

        Umat[:,np1]=np.real(np.fft.ifft(f_unp1))
        
        f_un=np.copy(f_unp1)
        f_NLnm1=np.copy(f_NLn)

        # instruction a completer question 5
        f_NLn= ...
    return t, x, Umat

**9.** Exécuter cette nouvelle fonction en choisissant ```nu=100```. Quel est l'impact sur le résultat?

In [ ]:
Tf=...
dt=...
M=...
nu=...
t,x,Umat = squelette_burgers_dissipation(nu,Tf,dt,M)

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.animation
plt.rcParams["animation.html"] = "jshtml"
plt.ioff()

fig = plt.figure()
ax = fig.add_subplot(1, 1, 1)
time_template = 't = %.2fs'
time_text = ax.text(2,1.1,'') 
lin = ax.plot(x,Umat[:,0])
ax.set_xlabel('x')
ax.set_ylabel('y')

#sortie graphique
def update(n):
    ax.cla()
    lin = ax.plot(x,Umat[:,n])
    time_text.set_text(time_template%t[n])
    return lin, time_text

step=100
matplotlib.animation.FuncAnimation(fig, update, frames=range(0,round(round(Tf/dt)),step), repeat=False)    


### Exercice : Instabilité de Rayleigh-Bénard


#### Implémentation

On fournit ci-dessous des fonctions qui permettent de créer les matrices creuses du problème et pour la visualisation. Il n'y **aucune modification** à apporter à ces fonctions mais il faut les exécuter au moins une fois.

In [ ]:
from scipy.sparse import coo_matrix,identity
import numpy as np

# Remplir cette fonction 
def MATcreate(lam,Mx,My):

    Ntot=Mx*(My+1)     #nombre de pts total
    Nint=Mx*(My-1)     #nombre de pts int

    dx=lam/Mx 
    dy=1/My
    
    
    #I: matrice unité 
    I=identity(Ntot,format="coo");

    #P: matrice de projection  sur les points intérieurs
    #1 sur la diagonale si pt intérieur, 0 autrement
    N_nonnuls=np.copy(Nint) 
    row=np.zeros(N_nonnuls)
    col=np.zeros(N_nonnuls)
    val=np.zeros(N_nonnuls)

    offset=-1  #indice offset -1
    for i in range(Mx):   # pour i allant de 0 à Mx-1 
        for j in range(1,My):   # pour j allant de 1 à My-1 
        
            ind=i*(My+1)+j
            row[offset+1]=ind
            col[offset+1]=ind
            val[offset+1]=1
            offset=offset+1   
            
    P=coo_matrix((val, (row, col)), shape=(Ntot, Ntot))        
    
    #PD: matrice de diffusion sur les points intérieurs
    #0 sur les lignes des points ext
    #[a,b,c,b,a] sur les lignes des point int
    a=1/(dx**2);
    b=1/(dy**2);
    c=-2*(a+b);

    N_nonnuls=5*Nint
    row=np.zeros(N_nonnuls)
    col=np.zeros(N_nonnuls)
    val=np.zeros(N_nonnuls)

    offset=-1  #indice offset -1
    for i in range(Mx):   # pour i allant de 0 à Mx-1 
        for j in range(1,My):   # pour j allant de 1 à My-1 
        
            #definir indices ip et im, pour gestion de la périodicité
            if i==Mx-1:
                ip=0
            else:
                ip=i+1
                
            if i==0:
                im=Mx-1
            else:
                im=i-1
                                
            #indices nouvelle numérotation
            ind=i*(My+1)+j
            indN=i*(My+1)+j+1
            indS=i*(My+1)+j-1
            indE=ip*(My+1)+j
            indO=im*(My+1)+j
        
            row[offset+(np.arange(1,6))]=[ind,ind,ind,ind,ind]
            col[offset+(np.arange(1,6))]=[indO,indS,ind,indN,indE]
            val[offset+(np.arange(1,6))]=[a,b,c,b,a]
            offset=offset+5 
    
    PD=coo_matrix((val, (row, col)), shape=(Ntot, Ntot)) 
    
    #PAx: matrice de dérivation selon x sur les points intérieurs
    #0 sur les lignes des points ext
    #[-1/(2*dx) ,1/(2*dx)] sur les lignes des point int 
    N_nonnuls=2*Nint
    row=np.zeros(N_nonnuls)
    col=np.zeros(N_nonnuls)
    val=np.zeros(N_nonnuls)

    d=1/(2*dx)
    
    offset=-1  #indice offset -1
    for i in range(Mx):   # pour i allant de 0 à Mx-1 
        for j in range(1,My):   # pour i allant de 1 à My-1 
        
            if i==Mx-1:
                ip=0
            else:
                ip=i+1
                
            if i==0:
                im=Mx-1
            else:
                im=i-1
                                
            #indices nouvelle numérotation
            ind=i*(My+1)+j
            indE=ip*(My+1)+j
            indO=im*(My+1)+j
        
            row[offset+(np.arange(1,3))]=[ind,ind]
            col[offset+(np.arange(1,3))]=[indO,indE]
            val[offset+(np.arange(1,3))]=[-d,d]
            offset=offset+2   
    
    PAx=coo_matrix((val, (row, col)), shape=(Ntot, Ntot))
    
    
    #PAy: matrice de dérivation selon y sur les points intérieurs
    #0 sur les lignes des points ext
    #[-1/(2*dy) ,1/(2*dy)] sur les lignes des point int 
    N_nonnuls=2*Nint 
    row=np.zeros(N_nonnuls)
    col=np.zeros(N_nonnuls)
    val=np.zeros(N_nonnuls)

    e=1/(2*dy)
    offset=-1  #indice offset -1
    for i in range(Mx):   # pour i allant de 0 à Mx-1 
        for j in range(1,My):   # pour i allant de 1 à My-1           
            
            ind=i*(My+1)+j
            indN=i*(My+1)+j+1
            indS=i*(My+1)+j-1
        
            row[offset+(np.arange(1,3))]=[ind,ind]
            col[offset+(np.arange(1,3))]=[indS,indN]
            val[offset+(np.arange(1,3))]=[-e,e]
            offset=offset+2   
    
    PAy=coo_matrix((val, (row, col)), shape=(Ntot, Ntot))
    
    return I,P,PD,PAx,PAy 

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.animation
from mpl_toolkits.axes_grid1 import make_axes_locatable
plt.rcParams["animation.html"] = "jshtml"
plt.ioff()

def init_plot():
    fig = plt.figure()
    plt.set_cmap('jet')
    ax = fig.subplots(nrows=2, ncols=1, sharex=True, sharey=True)
    time_template = 't = %.2fs'
    time_text = ax[0].text(2,1.1,'') 
    cont_T = ax[0].contourf(x_mat,y_mat,T_mat[:,:,0],20)
    ax[0].set_xlabel('x')
    ax[0].set_ylabel('y')
    ax[0].axis('equal')
    div = make_axes_locatable(ax[0])
    cax1 = div.append_axes('right', '5%', '5%')
    cont_om = ax[1].contourf(x_mat,y_mat,om_mat[:,:,0],20)
    ax[1].set_xlabel('x')
    ax[1].set_ylabel('y')
    ax[1].axis('equal')
    div = make_axes_locatable(ax[1])
    cax2 = div.append_axes('right', '5%', '5%')
    return fig, ax, cax1, cax2, cont_T, cont_om, time_text, time_template

#sortie graphique
def update(n):
    global cont_T, cont_om
    for c in cont_T.collections:
        c.remove()  # removes only the contours, leaves the rest intact
    for c in cont_om.collections:
        c.remove()  # removes only the contours, leaves the rest intact
    cont_T = ax[0].contourf(x_mat,y_mat,T_mat[:,:,n],20)
    cax1.cla() # clear current axes (colormap)
    fig.colorbar(cont_T, cax=cax1,label='T') # set new colormap with new values
    cont_om = ax[1].contourf(x_mat,y_mat,om_mat[:,:,n],20)
    cax2.cla() # clear current axes (colormap)
    fig.colorbar(cont_om, cax=cax2,label='omega') # set new colormap with new values
    time_text.set_text(time_template%t_save[n])
    return cont_T, cont_om, time_text


On va procéder à l'implémentation dans les cellules ci-dessous de ce schéma discret.

**5.** Implémenter les opérateurs de gauche et de droite de l'équation (12a).

**6.** Faire de même pour les opérateurs de l'équation (12b).

**7.** Implémenter l'opérateur de l'équation (12c).

**8.**  Implémenter la fonction courant $\psi_0$ correspondant à l'initiatialisation (si le champ $\psi_0$ n'a pas été trouvé, l'initialiser avec un champ aléatoire de faible amplitude). Initialiser la température avec un champ linéaire vérifiant les conditions aux limites.

**9.** Implémenter le vecteur colonne $ST$ permettant de prendre en compte les conditions au limites sur $\theta$. 


On va procéder ensuite à l'implémentation, dans la boucle temporelle, de l'équation de la chaleur simultanément à celles de $\omega-\psi$, sans couplage.


**10.** Implémenter le schéma de l'équation (12c) tenant compte des conditions aux limites.

**11.** Implémenter le schéma de l'équation (12b), en prenant bien en compte le terme source $ST$.


In [ ]:
from scipy.sparse.linalg import spsolve, splu

def convection(Re,Ra,lam,Tf,Mx,My,N,nsave):

    Lx=lam
    Ly=1
    dx=Lx/Mx
    dy=Ly/My
    dt=Tf/N

    Ntot=Mx*(My+1)
    
    #créer les matrices
    I,P,PD,PAx,PAy=MATcreate(lam,Mx,My)
    
    #(Q5) operateur de gauche et droite equation 12a
    Og_om=...
    Od_om=...
    #(Q6) operateur de gauche et droite equation 12b
    Og_T=...
    Od_T=...
    #(Q7) operateur de gauche equation 12c
    Og_psi=...
    
    #convertir format coo en csc format (pour utiliser spsolve ou superlu)
    Og_om=Og_om.tocsc()
    Od_om=Od_om.tocsc()
    Og_psi=Og_psi.tocsc()
    Og_T=Og_T.tocsc()
    Od_T=Od_T.tocsc()
    
    #factorisation LU des opérateurs de gauche (pour gagner en temps de calcul)
    #plus bas, on explique comment résoudre un système linéaire. 
    lu_om=splu(Og_om)     
    lu_psi=splu(Og_psi) 
    lu_T=splu(Og_T) 
    
    #tableaux vides pour enregistrer des champs aux différents instants
    #chaque nsave pas de temps
    N_save=N//nsave+1    #nombre total de champs sauvegardés
    T_save=np.zeros([Ntot,N_save])
    om_save=np.zeros([Ntot,N_save])
    t_save=np.zeros(N_save)
    
    #(Q8) initialisation
    psin=np.zeros(Ntot)
    Tn=np.zeros(Ntot)
    for i in range(Mx):
        for j in range(My):
            ind=i*(My+1)+j
            x=i*dx
            y=j*dy
            psin[ind]=...
            Tn[ind]=...
    
    omn=-PD.dot(psin)             #utiliser la matrice de diffusion pour le calculer à partir de psin

    #indices des points de bords haut et bas
    ind_haut=np.arange(0,Mx)*(My+1)+My
    ind_bas=np.arange(0,Mx)*(My+1)

    #(Q9) conditions aux limites pour T
    ST=np.zeros(Ntot)
    ST[ind_bas]=...

    #initialisation du terme non-linéaire
    NLn=-PAy.dot(psin)*PAx.dot(omn)+PAx.dot(psin)*PAy.dot(omn)
    NLnm1=np.copy(NLn)           #dans la boucle principale, on code le schéma d'adams-bashfort 2 pour le terme NL
                                 #et cela nécessite NL^{n} et NL^{n-1}. Ici on dit que NL^{-1} = NL^0 
                                 #afin de faire un premier pas de temps Euler explicite

    #initialisation du terme non-linéaire T
    NLTn=-PAy.dot(psin)*PAx.dot(Tn)+PAx.dot(psin)*PAy.dot(Tn)
    NLTnm1=np.copy(NLTn)

    #enregistrer le champ initial dans les grands tableaux
    T_save[:,0]=Tn
    om_save[:,0]=omn 
    t_save[0]=0

    compte=0  #indice du dernier pas de temps sauvegardé 
    t=0
    #boucle d'avancement temporel
    for n in range(1,N+1):  #pour n = 1 à N
        t=t+dt
        
        #on doit trouver omega^{n+1} comme la solution d'un systeme linéaire
        #on construit d'abord le membre de droite de l'équation de vorticité 
        # (avec omn, matrices et termes NL)
        #(Q13) puis avec le terme source de Boussinesq
        eqom_membredroite=Od_om.dot(omn)+dt/2*(3*NLn-NLnm1)
        
        #on trouve la solution du système lineare Og_om*om^{n+1}=eqom_membredroite. 
        #Le résultat sera le nouveau état de vorticité, et ici choisit d'écraser la variable omn
        #
        #Comment trouver la solution? Si lu=splu(Og), alors la solution f du système linéaire Og*f = g 
        #s'écrit tout simplement f=lu.solve(g) en python. 
        omn=lu_om.solve(eqom_membredroite)
    
        #Dans omn on a la nouvelle vorticité om^{n+1}. 

        #(Q10) Trouver maintenant de la même manière, la solution du système linéaire 
        # qui donne la nouvelle fonction de courant. On écrase la variable psin
        psin=lu_psi.solve(...)

        #(Q11) on doit trouver T^{n+1} comme la solution d'un systeme linéaire
        # on construit d'abord le membre de droite de l'équation de température
        # (avec Tn, matrices, termes NL et terme source)
        eqT_membredroite=...

        #on trouve la solution du système lineare 
        # Og_T*T^{n+1}=eqT_membredroite. 
        Tn=lu_T.solve(eqT_membredroite)

        #enregistrer les champs chaque nsave pas de temps 
        if  ((n%nsave)==0):
            T_save[:,compte+1]=Tn
            om_save[:,compte+1]=omn
            t_save[compte+1]=t
            compte=compte+1
            
        #pour préparer le prochain pas de temps, 
        NLnm1=np.copy(NLn)       #le terme NL à temps n-1 devient le terme NL a temps n

        #et on doit aussi calculer un nouveau terme NL, avec les nouveaux champs
        NLn=-PAy.dot(psin)*PAx.dot(omn)+PAx.dot(psin)*PAy.dot(omn)

        #pour préparer le prochain pas de temps, 
        NLTnm1=np.copy(NLTn)       #le terme NL à temps n-1 devient le terme NL a temps n

        #et on doit aussi calculer un nouveau terme NL, avec les nouveaux champs
        NLTn=-PAy.dot(psin)*PAx.dot(Tn)+PAx.dot(psin)*PAy.dot(Tn)

        
    ## Cette section sert à créer les tableaux qui permettent une future visualisation
    # A laisser la sous cette forme. Attention: ça peut donner un message d'erreur 
    # (matrices de dimension pas compatabiles) si vous vous êtes trompé dans le code. 
    T_mat=np.zeros([My+1,Mx,N_save])  
    om_mat=np.zeros([My+1,Mx,N_save])   
    
    for compte in range(0,N_save): 
        for i in range(0,Mx):      
            for j in range(0,My+1): 
                ind=i*(My+1)+j
                T_mat[j,i,compte]=T_save[ind,compte]  
                om_mat[j,i,compte]=om_save[ind,compte]  

    #maillage 2D réduit
    x_mat,y_mat=np.meshgrid(np.linspace(0,Lx-dx,Mx),np.linspace(0,Ly,My+1))        

    return x_mat,y_mat,T_mat,om_mat,t_save


**12.** Pour vérifier l'implémentation correcte de ces schémas, lancer la cellule ci-dessous qui va exécuter la fonction ```convection``` avec les bons paramètres et jouer l'animation du champ de température au cours du temps. 

Sachant que $Ra=0$, il ne doit pas y avoir d'écoulement et on doit s'attendre à une solution stationnaire pour $\theta$ qui correspond à la conduction de la chaleur entre les deux murs. Quelle est la solution théorique attendue? Donner l'équation de $\theta(y)$.


In [ ]:
#paramètres physiques
Re,Ra,lam,Tf =1,0,np.pi,0.1

#paramètres numériques
Mx,My,N,nsave=100,100,10,1

#lancer le code
x_mat,y_mat,T_mat,om_mat,t_save=convection(Re,Ra,lam,Tf,Mx,My,N,nsave)

In [ ]:
#visualisation
step=1
fig, ax, cax1, cax2, cont_T, cont_om, time_text, time_template=init_plot()
matplotlib.animation.FuncAnimation(fig, update, frames=range(0,round(N/nsave),step), repeat=False)    

On prend en compte maintenant le terme de couplage de Boussinesq.


**13.** Rajouter maintenant le terme discrétisé à la question 2.

**14.** Vérifier l'implémentation correcte de ce terme en modifiant le nombre de Rayleigh dans la cellule ci-dessous et en le prenant égal à 1000. Qu'observe-t-on?


In [ ]:
#paramètres physiques
Re,Ra,lam,Tf =1,0000,np.pi,5

#paramètres numériques
Mx,My,N,nsave=100,100,500,10

#lancer le code
x_mat,y_mat,T_mat,om_mat,t_save=convection(Re,Ra,lam,Tf,Mx,My,N,nsave)

In [ ]:
#visualisation
step=1
matplotlib.animation.FuncAnimation(fig, update, frames=range(0,round(N/nsave),step), repeat=False)    